## coding

In [1]:
import ee
ee.Authenticate()
ee.Initialize(project='pc399-edu-dises')

Enter verification code:  4/1Adeu5BXun_caNPMarVGDdB71au0VaV_tSI1fvqWPZrNZDc-2a4t-YCCqGkQ



Successfully saved authorization token.


In [2]:
import geemap

In [3]:
test_area_geom = ee.Geometry.Polygon([
    [107.4, 14.4],  # x0, y0
    [107.4, 14.7],  # x0, y1
    [107.6, 14.7],
    [107.6, 14.4]
])

# test_area_ft = ee.Feature(test_area_geom)

### read in one of Robert's data

In [50]:
tcc_raw = ee.Image('users/liutc/SIG/DISES/matching/data/raw/camb_tcc_2005_mean_300m')
# TODO: upload LC, disturbance magnitude, yod GeoTIFF to EE and import just as tcc

In [23]:
tcc = tcc_raw.clip(test_area_ft)

In [24]:
tcc

In [86]:
pixel_count = tcc.reduceRegion(
    reducer=ee.Reducer.count()
)

In [87]:
pixel_count

In [40]:
ee.batch.Export.image.toAsset(
    image=tcc,
    description='test area camb_tcc_2005_mean_300m',
    assetId='projects/pc399-edu-dises/assets/matching/data/test_tcc_2005_mean_300m',
    maxPixels=1e13  
).start()

### process EE data to match with Robert's

In [4]:
country = 'Cambodia'
aoi_geom = ee.FeatureCollection("USDOS/LSIB/2017").filter(ee.Filter.eq('COUNTRY_NA', country)).geometry()

In [5]:
aoi_geom

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Collection.geometry",
    "arguments": {
      "collection": {
        "functionInvocationValue": {
          "functionName": "Collection.filter",
          "arguments": {
            "collection": {
              "functionInvocationValue": {
                "functionName": "Collection.loadTable",
                "arguments": {
                  "tableId": {
                    "constantValue": "USDOS/LSIB/2017"
                  }
                }
              }
            },
            "filter": {
              "functionInvocationValue": {
                "functionName": "Filter.equals",
                "arguments": {
                  "leftField": {
                    "constantValue": "COUNTRY_NA"
                  },
                  "rightValue": {
                    "constantValue": "Cambodia"
                  }
                }
              }
            }
          }
        }
      }
    }
  }
})

#### slope & aspect

##### compute slope & aspect from DEM

In [6]:
dem = ee.Image("USGS/SRTMGL1_003").clip(aoi_geom.buffer(1000)).clip(test_area_geom)

In [7]:
dem

In [8]:
terrain = ee.Algorithms.Terrain(dem)
slope = terrain.select('slope')
aspect = terrain.select('aspect')

##### slope

In [10]:
slope

In [11]:
# Check min and max
statistics = slope.reduceRegion(
    reducer=ee.Reducer.minMax()
)
min_value = statistics.get('slope_min')
max_value = statistics.get('slope_max')
(min_value.getInfo(), max_value.getInfo())

(0, 66)

In [9]:
slope.projection()

In [10]:
slope.projection().nominalScale()

##### match with tree canopy cover

In [28]:
proj = tcc.projection()

In [29]:
proj

In [26]:
ee.Projection("EPSG:32648").atScale(300)

In [30]:
slope_mean = slope.reduceResolution(
    reducer=ee.Reducer.mean(),
    maxPixels=1024
)

In [17]:
slope_mean

In [31]:
# Check min and max
statistics = slope_mean.reduceRegion(
    reducer=ee.Reducer.minMax()
)
min_value = statistics.get('slope_min')
max_value = statistics.get('slope_max')
(min_value.getInfo(), max_value.getInfo())

(0, 66)

In [32]:
slope_mean_proj = slope_mean.reproject(proj)

In [19]:
# Check min and max
statistics = slope_mean_proj.reduceRegion(
    reducer=ee.Reducer.minMax()
)
min_value = statistics.get('slope_min')
max_value = statistics.get('slope_max')
(min_value.getInfo(), max_value.getInfo())

(3.27527420100973, 34.03390261099777)

In [38]:
ee.batch.Export.image.toAsset(
    image=slope_mean_proj,
    description='test area mean slope matched with camb_tcc_2005_mean_300m',
    assetId='projects/pc399-edu-dises/assets/matching/data/test_slope_mean_proj',
    maxPixels=1e13  
).start()

In [6]:
Map = geemap.Map(center=(12.5, 104.8), zoom=7)  # , add_google_map=False)

In [7]:
Map.addLayer(aoi_geom)
Map

Map(center=[12.5, 104.8], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

In [20]:
Map.addLayer(tcc, name='tree canopy cover')

NameError: name 'tcc' is not defined

In [ ]:
# Map.addLayer(dem, name='dem')

In [21]:
# Map.addLayer(slope, name='slope')

In [20]:
# Map.addLayer(slope_mean, name='slope mean')

In [21]:
# Map.addLayer(slope_mean_proj, name='slope mean reprojected')

In [22]:
# Map.addLayer(slope_mean_proj_oneline, name='slope mean reprojected in oneline')

In [30]:
# Map.addLayer(combo, name='tree canopy cover + slope mean reprojected')

In [32]:
# Map.addLayer(slope_aligned, name='slope mean reprojected, aligned with tree canopy cover')

In [41]:
# Map.addLayer(lc, name='land cover')

In [43]:
# Map.addLayer(combo2, name='tree canopy cover + slope mean reprojected + land cover')

In [22]:
# Map

Map(center=[12.5, 104.8], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

### read in more Robert's data

In [89]:
lc_raw = ee.Image('users/liutc/SIG/DISES/matching/data/raw/camb_LC_2005_300m')

In [44]:
lc_raw

In [90]:
lc = lc_raw.clip(test_area_ft)

In [58]:
lc

### compile values from all layers and test tabularization

#### compile

In [41]:
combo = tcc.addBands(slope_mean_proj)

In [27]:
slope_mean_proj.bandNames()

In [29]:
combo

In [42]:
task = ee.batch.Export.image.toAsset(
    image=combo,
    assetId='projects/pc399-edu-dises/assets/matching/data/test_tcc_2005_mean_300m_w_slope_mean_proj',
    maxPixels=1e13
)
task.start()

In [31]:
slope_aligned = combo.select('slope')

In [42]:
# combo2 = combo.addBands(lc)

In [61]:
# task = ee.batch.Export.image.toAsset(
#     image=combo2.clip(test_area_geom),
#     assetId='users/tianchi2liu/combo2',
#     # scale: scale,
#     # region: aoi,
#     # crs=proj,
#     maxPixels=1e13
# )
# task.start()

#### test tabularization

In [44]:
combo_fc = combo.sample(
    dropNulls=False,
    geometries=True
)

In [45]:
combo_fc

C:\Users\tianc\anaconda3\envs\DISES\lib\site-packages\eerepr\repr.py:57: UserWarning: Getting info failed with: 'Collection query aborted after accumulating over 5000 elements.'. Falling back to string repr.
  warn(f"Getting info failed with: '{e}'. Falling back to string repr.")


In [49]:
combo_fc.limit(10)

In [79]:
combo_fc.size().getInfo()

7807

In [52]:
task = ee.batch.Export.image.toAsset(
    image=combo,
    assetId='projects/pc399-edu-dises/assets/matching/data/tcc_2005_mean_300m_w_test_slope_mean_proj',
    maxPixels=1e13
)
task.start()

In [64]:
task = ee.batch.Export.table.toAsset(**{
    'collection': combo_fc,
    'description':'exportToTableAsset',
    'assetId': 'projects/pc399-edu-dises/assets/matching/data/test_tcc_2005_mean_300m_w_slope_mean_proj_tbl',
})
task.start()

#### tests: data for the entire country are too large to export

In [51]:
combo2 = tcc_raw.addBands(slope_mean_proj)  # instead of tcc

In [53]:
combo2_fc = combo2.sample(
    dropNulls=False,
    geometries=True
)

In [72]:
task = ee.batch.Export.table.toAsset(**{
    'collection': combo2_fc,
    'description':'exportToTableAsset',
    'assetId': 'projects/pc399-edu-dises/assets/matching/data/tcc_2005_mean_300m_w_test_slope_mean_proj_tbl',
})
task.start()
# Error: Reprojection output too large (9144x10048 pixels). (Error code: 3)

In [71]:
task = ee.batch.Export.table.toDrive(**{
  'collection': combo2_fc,
  'fileFormat': 'CSV'
})
task.start()  
# Error: Reprojection output too large (10272x10049 pixels). (Error code: 3)

In [76]:
combo2_sample_fc = combo2_fc.randomColumn().filter('random < 0.0001')

In [78]:
combo2_sample_fc.size().getInfo()
# Reprojection output too large (9144x10048 pixels)

EEException: Reprojection output too large (9144x10048 pixels).

In [80]:
combo2_dic = combo2_fc.toDictionary().getInfo()
# Reprojection output too large (9144x10048 pixels)

EEException: Reprojection output too large (9144x10048 pixels).

### mask all non-forest pixels in all layers

In [91]:
combo3 = combo.addBands(lc)

In [93]:
combo3

In [94]:
mask = lc.eq(0)  # 0: evergreen

In [95]:
mask  # 1==evergreen; 0==other

In [115]:
mask_mean = mask.reduceRegion(
    reducer=ee.Reducer.mean()
)

In [116]:
mask_mean  # percent pixels that won't be masked out

In [107]:
combo3_masked = combo3.updateMask(mask)

In [112]:
combo3_masked

### tabularize

In [110]:
combo3_masked_fc = combo3_masked.sample(
    dropNulls=False,
    geometries=True
)

In [111]:
task = ee.batch.Export.table.toAsset(**{
    'collection': combo3_masked_fc,
    'assetId': 'projects/pc399-edu-dises/assets/matching/data/test_evergreen_covar_tbl',
})
task.start()

## mapping

In [119]:
# for ipyleaflet
esri_102016_proj = {
    "name": "ESRI:102016",
    "custom": True,
    "proj4def": "+proj=aeqd +lat_0=90 +lon_0=0 +x_0=0 +y_0=0 +datum=WGS84 +units=m +no_defs +type=crs",
    "origin": [0.0 -5294789.78],
    "bounds": [[-8046094.81, 1819060.18], [988364.71, 3511186.72]],  # TODO: update bounds
    "resolutions": [8192.0, 4096.0, 2048.0, 1024.0, 512.0, 256.0],  # TODO: update resolutions
}

#### geemap not working in Jupyter Lab, but worked in Google Colab (geemap relies on ipyleaflet)

In [6]:
Map = geemap.Map(center=(12.5, 104.8), zoom=7)  # , add_google_map=False)

In [7]:
Map.addLayer(aoi_geom)
Map

Map(center=[12.5, 104.8], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

In [20]:
Map.addLayer(tcc, name='tree canopy cover')

NameError: name 'tcc' is not defined

In [ ]:
# Map.addLayer(dem, name='dem')

In [21]:
# Map.addLayer(slope, name='slope')

In [20]:
# Map.addLayer(slope_mean, name='slope mean')

In [21]:
# Map.addLayer(slope_mean_proj, name='slope mean reprojected')

In [22]:
# Map.addLayer(slope_mean_proj_oneline, name='slope mean reprojected in oneline')

In [30]:
# Map.addLayer(combo, name='tree canopy cover + slope mean reprojected')

In [32]:
# Map.addLayer(slope_aligned, name='slope mean reprojected, aligned with tree canopy cover')

In [41]:
# Map.addLayer(lc, name='land cover')

In [43]:
# Map.addLayer(combo2, name='tree canopy cover + slope mean reprojected + land cover')

In [22]:
# Map

Map(center=[12.5, 104.8], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

#### geemap projection check

In [ ]:
tcc_img = ee.Image('users/liutc/SIG/DISES/matching/data/raw/camb_tcc_2005_mean_300m') 
tcc_epsg102016_img = ee.Image('users/liutc/SIG/DISES/matching/data/raw/camb_tcc_2005_mean_300m_epsg102016')
tcc_epsg3413_img = ee.Image('users/liutc/SIG/DISES/matching/data/raw/camb_tcc_2005_mean_300m_epsg3413')
# see Asset details for more info

In [ ]:
tcc_img

In [ ]:
tcc_epsg102016_img

In [ ]:
tcc_epsg3413_img

##### projection

In [ ]:
tcc_img.projection()

In [ ]:
tcc_epsg102016_img.projection()

##### scale

In [ ]:
tcc_img.projection().nominalScale()

In [ ]:
tcc_epsg102016_img.projection().nominalScale()

##### map

In [ ]:
# Map = geemap.Map(center=(12.5, 104.8), zoom=7)  # Cambodia
# Map = geemap.Map(center=(12.5, 104.8), zoom=7, crs=projections.EPSG4326)
Map = geemap.Map(center=(12.5, 104.8), zoom=7, add_google_map=False)
# Map = geemap.Map(center=(12.5, 104.8), zoom=7, crs=esri_102016_proj)

Map.addLayer(tcc_img, name='tree canopy cover')
# Map.addLayer(tcc_epsg102016_img, name='tree canopy cover reprojected')
Map.addLayer(tcc_epsg3413_img, name='tree canopy cover reprojected')

Map

Map(center=[12.5, 104.8], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

#### ipyleaflet not working in Jupyter Lab, but worked in Google Colab

In [ ]:
import ipyleaflet

In [ ]:
def GetTileLayerUrl(ee_image_object):
    map_id = ee.Image(ee_image_object).getMapId()
    tile_fetcher = map_id['tile_fetcher']
    return tile_fetcher.url_format

In [10]:
m = ipyleaflet.Map()
m

Map(center=[0.0, 0.0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_t…

In [ ]:
# map tcc_epsp*_img which were 
m = ipyleaflet.Map(
    center=(12.5, 104.8),
    zoom=7,
    # zoom=0,
    layers=(ipyleaflet.TileLayer(url=GetTileLayerUrl(tcc_epsg3413_img)),),
    # layers=(ipyleaflet.TileLayer(url=GetTileLayerUrl(tcc_epsg102016_img)),),
)
m

Map(center=[12.5, 104.8], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_ou…

In [ ]:
m = ipyleaflet.Map(
    # center=(12.5, 104.8),
    # zoom=7,
    center=(90, 0),
    zoom=0,
    # basemap=ipyleaflet.basemaps.Esri.AntarcticBasemap,
    # crs=ipyleaflet.projections.EPSG3031.ESRIBasemap
    basemap=ipyleaflet.basemaps.NASAGIBS.BlueMarble3413,
    crs=ipyleaflet.projections.EPSG3413.NASAGIBS,
)

m.add_layer(
    # ipyleaflet.TileLayer(url=GetTileLayerUrl(tcc_epsg102016_img)) #, crs=esri_102016_proj)
    ipyleaflet.TileLayer(url=GetTileLayerUrl(tcc_epsg3413_img), crs=ipyleaflet.projections.EPSG3413.NASAGIBS)
)

m

Map(center=[90, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

#### folium

In [14]:
import folium

In [15]:
# Add custom basemaps to folium
basemaps = {
    'Google Maps': folium.TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Maps',
        overlay = True,
        control = True
    ),
    'Google Satellite': folium.TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=s&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Satellite',
        overlay = True,
        control = True
    ),
    'Google Terrain': folium.TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=p&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Terrain',
        overlay = True,
        control = True
    ),
    'Google Satellite Hybrid': folium.TileLayer(
        tiles = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',
        attr = 'Google',
        name = 'Google Satellite',
        overlay = True,
        control = True
    ),
    'Esri Satellite': folium.TileLayer(
        tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
        attr = 'Esri',
        name = 'Esri Satellite',
        overlay = True,
        control = True
    )
}

In [16]:
# Define a method for displaying Earth Engine image tiles on a folium map.
def add_ee_layer(self, ee_object, vis_params, name):
    
    try:    
        # display ee.Image()
        if isinstance(ee_object, ee.image.Image):    
            map_id_dict = ee.Image(ee_object).getMapId(vis_params)
            folium.raster_layers.TileLayer(
            tiles = map_id_dict['tile_fetcher'].url_format,
            attr = 'Google Earth Engine',
            name = name,
            overlay = True,
            control = True
            ).add_to(self)
        # display ee.ImageCollection()
        elif isinstance(ee_object, ee.imagecollection.ImageCollection):    
            ee_object_new = ee_object.mosaic()
            map_id_dict = ee.Image(ee_object_new).getMapId(vis_params)
            folium.raster_layers.TileLayer(
            tiles = map_id_dict['tile_fetcher'].url_format,
            attr = 'Google Earth Engine',
            name = name,
            overlay = True,
            control = True
            ).add_to(self)
        # display ee.Geometry()
        elif isinstance(ee_object, ee.geometry.Geometry):    
            folium.GeoJson(
            data = ee_object.getInfo(),
            name = name,
            overlay = True,
            control = True
        ).add_to(self)
        # display ee.FeatureCollection()
        elif isinstance(ee_object, ee.featurecollection.FeatureCollection):  
            ee_object_new = ee.Image().paint(ee_object, 0, 2)
            map_id_dict = ee.Image(ee_object_new).getMapId(vis_params)
            folium.raster_layers.TileLayer(
            tiles = map_id_dict['tile_fetcher'].url_format,
            attr = 'Google Earth Engine',
            name = name,
            overlay = True,
            control = True
        ).add_to(self)
    
    except:
        print("Could not display {}".format(name))
    
# Add EE drawing method to folium.
folium.Map.add_ee_layer = add_ee_layer

In [113]:
# Set visualization parameters.
vis_params = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']}

# Create a folium map object.
my_map = folium.Map(location=(12.5, 104.8), zoom_start=7, height=500)
print(1)

# # Add custom basemaps
# basemaps['Google Maps'].add_to(my_map)
# basemaps['Google Satellite Hybrid'].add_to(my_map)

# Add layers to the map object.
# my_map.add_ee_layer(combo_fc, vis_params, 'combo_fc')
# my_map.add_ee_layer(combo2_fc, vis_params, 'combo2_fc')
my_map.add_ee_layer(mask, {'min':0, 'max':1}, 'mask')
my_map.add_ee_layer(combo3_masked, {'min':0, 'max':90}, 'combo3_masked')
print(2)

# Add a layer control panel to the map.
my_map.add_child(folium.LayerControl())
print(3)

# # Add fullscreen button  # errors
# plugins.Fullscreen().add_to(my_map)

1
2
3


In [114]:
# Display the map.
display(my_map)